In [ ]:
!pip install transformers datasets accelerate pipeline

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
!pip install SentencePiece

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
from transformers import AutoTokenizer, LongT5ForConditionalGeneration, pipeline
from torch.utils.data import Dataset

checkpoint = "pszemraj/long-t5-tglobal-base-16384-book-summary"
tokenizer = AutoTokenizer.from_pretrained(checkpoint)
model = LongT5ForConditionalGeneration.from_pretrained(checkpoint)
summarizer = pipeline("summarization", model=model, tokenizer=tokenizer)

In [5]:
import os
from csv import DictReader, DictWriter
from tqdm.auto import tqdm
from torch.utils.data import DataLoader
import numpy as np

def read(filepath):
    rows = []
    with open(filepath, "r", encoding='utf-8') as table:
        r = DictReader(table)

        for line in r:
            rows.append(line)
    return rows


def write(filepath, dictionary):
    with open(filepath, "w", encoding='utf-8', newline='') as table:
        fieldnames = list(dictionary[0].keys())
        print(fieldnames)
        writer = DictWriter(table, fieldnames=fieldnames)
        writer.writeheader()

        for line in dictionary:
            writer.writerow(line)

class ArticleDataset(Dataset):
  def __init__(self, articles):
    self.articles = articles
  
  def __len__(self):
      return len(self.articles)

  def __getitem__(self, i):
      return self.articles[i]

def create_summaries(path):
  for file in os.listdir(path):
    if file.endswith("_bodies.csv"):
      newFileName = str(file)
      newFileName = newFileName.replace("_bodies.csv", "_summaries.csv")
      filepath = os.path.join(path, file)
      articles = read(filepath)
      print(file)
      
      articleDataset = ArticleDataset(articles)
      dataLoader = DataLoader(articleDataset, batch_size=16, shuffle=True, num_workers=8)

      dataToWrite = []
      IDs = np.array([])
      summaries = np.array([])
      for batch in tqdm(dataLoader):
        out = summarizer(batch["articleBody"], max_length = 130, min_length=30)
        print(out)        
        IDs = np.append(IDs,batch["Body ID"])
        summaries = np.append(summaries,out)
        
              
      for index, summary in enumerate(summaries):
        keyValue = {
            "Body ID": int(IDs[index]),
            "articleSummary": summaries[index]['summary_text']
        }
        print(keyValue)
        dataToWrite.append(keyValue)

      dataToWrite = sorted(dataToWrite, key=lambda d: d['Body ID']) 
      print(dataToWrite)

      newFilePath = os.path.join(path, newFileName)
      write(newFilePath, dataToWrite)


create_summaries("fnc-1")

test_bodies.csv


  0%|          | 0/57 [00:00<?, ?it/s]

Your max_length is set to 130, but you input_length is only 37. You might consider decreasing max_length manually, e.g. summarizer('...', max_length=18)
/usr/local/lib/python3.7/dist-packages/transformers/modeling_utils.py:668: FutureWarning: The `device` argument is deprecated and will be removed in v5 of Transformers.
  "The `device` argument is deprecated and will be removed in v5 of Transformers.", FutureWarning
Your max_length is set to 130, but you input_length is only 22. You might consider decreasing max_length manually, e.g. summarizer('...', max_length=11)
Your max_length is set to 130, but you input_length is only 26. You might consider decreasing max_length manually, e.g. summarizer('...', max_length=13)


[{'summary_text': "While some Israeli political leaders respond positively to reports of al-sisi's offer to expand the occupied territory, Abbas rejects the reports. Abbas says that the reports are false and that the report was made out of deception."}, {'summary_text': 'The British government has learned that the "masked executioners" Jihadi John, a British member of the banned Islamic State, has been wounded in a recent air strike. According to reports published by the Mail, the British-controlled group is responsible for the deaths of three British journalists and aid workers. Jalman al-Brittani is considered one of the most powerful members of the group.'}, {'summary_text': 'Al-Brittani has been killed in an airstrikes by the United States in Syria. He reportedly says that he was killed during the attack and is reported dead.'}, {'summary_text': 'A police officer in a small village near wenling city says that his penis has been stolen while he was asleep. The local man, Fei Lin, te

Your max_length is set to 130, but you input_length is only 25. You might consider decreasing max_length manually, e.g. summarizer('...', max_length=12)


...

[{'summary_text': "An Indian wedding has been postponed due to a sudden illness. The bride is furious that her family has not been told about Mr. Kishore's condition, and she chooses Harpal Singh as the new groom for the occasion. After the wedding, the whole family quarrels over who gets to wear the bridal dress. A police official reports that two guests are arrested but that both families have resolved the matter."}, {'summary_text': "The company is nearing an acquisition of its social platform, Path, according to Pandodaily. Morin and his company are close to making a big deal, but they're not sure how big the purchase will be."}, {'summary_text': "The new line of watches will come with safes to keep them safe from theft, and they'll also have a way to weigh the gold in each watch to ensure no gold is removed before it's returned."}, {'summary_text': 'The narrator tells us that the fake story is from a "fake sub-mediUM of NBCcalled NBCtoday.com" and spreads like wildfire without any

Your max_length is set to 130, but you input_length is only 17. You might consider decreasing max_length manually, e.g. summarizer('...', max_length=8)


[{'summary_text': 'The company is set to buy Swedish game maker Mojang for $2.5B in order to broaden its offering of next-gen games.'}, {'summary_text': 'The British triumvir Jihadi Al-Bawdi has been injured by a US air strike. He attended a meeting of the Islamic State in an area near the Syria border last Saturday, and reports have come from the Foreign Office that he is seriously wounded. According to reports, at least 30 tribesmen from various partsof Syria and Iraq gather to pledge all loyalty to Al-Barbadi. A nurse who treated both Jihad John and Al- Barbadas wounds him, but the doctor says that Jalman was responsible for the killing of the journalists. They are'}, {'summary_text': 'The three soldiers are reported missing from joint base Cape cod on Saturday after being seen at another mall. Major Jomohama Arash, captain Mohammad Netir Askerzada , and Captain Aminyare have been found crossing the border to Canada. They were not considered dangerous by the public because they had 

Your max_length is set to 130, but you input_length is only 105. You might consider decreasing max_length manually, e.g. summarizer('...', max_length=52)


[{'summary_text': 'The highly anticipated "apple watch" is finally coming to market in April. Cook says that he\'s excited about the new device because there\'s a large number of potential customers looking for one.'}, {'summary_text': 'The narrator tells us that Buenos Aires\' President, Christina Fernandez de-Kirchner, is planning to adopt werewolves. According to some folklore, the seventh child will turn into "the fearful el Lobison" on the first day after his 13th birthday; this myth predicts that the child will become a giant beast at midnight during every full moon. Other bits of information about the feared creature are also included in the article. In 1907, the sitting president adopted one of these babies as their godparent and then extended the practice to other'}, {'summary_text': 'The president of Buenos Aires, Christina Fernandeze, has accepted an officially Jewish godson named Yair Talwil. He was originally adopted under a 1920 law that prevented the death of boys from b

In [6]:
!mkdir -p /content/drive/MyDrive/long-t5-tglobal/fnc-1/
!cp -R fnc-1 /content/drive/MyDrive/long-t5-tglobal/fnc-1/